<a href="https://colab.research.google.com/github/globalexplorer/Machine-Learning-Pipeline-for-FIFA-Wages/blob/main/Machine_Learning_Pipeline_for_FIFA_Wages_using_PySpark_and_MLib.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Install Spark, load libraries and file, initiate Spark

In [1]:
!apt-get install openjdk-8-jdk-headless -qq > /dev/null
!wget -q https://downloads.apache.org/spark/spark-2.4.7/spark-2.4.7-bin-hadoop2.7.tgz
!tar xf spark-2.4.7-bin-hadoop2.7.tgz
!pip install -q findspark

In [2]:
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-2.4.7-bin-hadoop2.7"
import findspark
findspark.init()
from google.colab import files
from pyspark.sql import SparkSession
from pyspark.ml.feature import VectorAssembler
from pyspark.sql.functions import isnan, when, count, col, lit
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
from pyspark.ml.tuning import CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.tuning import ParamGridBuilder


In [3]:
sc = SparkSession.builder.master('local[*]').getOrCreate()

In [4]:
!ls
files.upload()

sample_data  spark-2.4.7-bin-hadoop2.7	spark-2.4.7-bin-hadoop2.7.tgz


Saving FifaTrainNew.csv to FifaTrainNew.csv


{'FifaTrainNew.csv': b"Ob,WageNew,Age,Nationality,Overall,Potential,Club,Special,Preferred Foot,International Reputation,Weak Foot,Skill Moves,Work Rate,Body Type,Real Face,Position,Joined,Contract Valid Until,Height,Weight,LS,ST,RS,LW,LF,CF,RF,RW,LAM,CAM,RAM,LM,LCM,CM,RCM,RM,LWB,LDM,CDM,RDM,RWB,LB,LCB,CB,RCB,RB,Crossing,Finishing,HeadingAccuracy,ShortPassing,Volleys,Dribbling,Curve,FKAccuracy,LongPassing,BallControl,Acceleration,SprintSpeed,Agility,Reactions,Balance,ShotPower,Jumping,Stamina,Strength,LongShots,Aggression,Interceptions,Positioning,Vision,Penalties,Composure,Marking,StandingTackle,SlidingTackle,GKDiving,GKHandling,GKKicking,GKPositioning,GKReflexes\r\n1,26735,25,Austria,77,80,FC Augsburg,1971,Left,2,3,2,High/ Medium,Stocky,No,LCB,31-Aug-16,2021,6'0,183lbs,64+2,64+2,64+2,60+2,62+2,62+2,62+2,60+2,62+2,62+2,62+2,62+2,67+2,67+2,67+2,62+2,68+2,73+2,73+2,73+2,68+2,70+2,76+2,76+2,76+2,70+2,53,48,77,63,49,55,58,63,81,62,63,73,62,68,62,83,85,72,83,71,82,76,61,65,64,65,77,78,77,1

In [45]:
data = sc.read.csv('FifaTrainNew.csv', inferSchema=True, header=True)

In [46]:
data.printSchema()
data.describe().toPandas().transpose()

root
 |-- Ob: integer (nullable = true)
 |-- WageNew: integer (nullable = true)
 |-- Age: integer (nullable = true)
 |-- Nationality: string (nullable = true)
 |-- Overall: integer (nullable = true)
 |-- Potential: integer (nullable = true)
 |-- Club: string (nullable = true)
 |-- Special: integer (nullable = true)
 |-- Preferred Foot: string (nullable = true)
 |-- International Reputation: string (nullable = true)
 |-- Weak Foot: string (nullable = true)
 |-- Skill Moves: string (nullable = true)
 |-- Work Rate: string (nullable = true)
 |-- Body Type: string (nullable = true)
 |-- Real Face: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- Joined: string (nullable = true)
 |-- Contract Valid Until: string (nullable = true)
 |-- Height: string (nullable = true)
 |-- Weight: string (nullable = true)
 |-- LS: string (nullable = true)
 |-- ST: string (nullable = true)
 |-- RS: string (nullable = true)
 |-- LW: string (nullable = true)
 |-- LF: string (nullable = true

0                   1  ...            3         4
summary        count                mean  ...          min       max
Ob             12745              6373.0  ...            1     12745
WageNew        12745  11432.671479011377  ...            6    650305
Age            12745  25.048646528050217  ...           16        44
Nationality    12745                None  ...  Afghanistan  Zimbabwe
...              ...                 ...  ...          ...       ...
GKDiving       12745  16.684347210199103  ...            1        NA
GKHandling     12745   16.43920673644448  ...            1        NA
GKKicking      12745  16.274887857086647  ...            1        NA
GKPositioning  12745  16.444558117572992  ...            1        NA
GKReflexes     12745   16.76989061147399  ...            1        NA

[81 rows x 5 columns]

In [47]:
def replace(col, val):
  return when(col != val, col).otherwise(lit(None))
  
for col_name in data.columns:
  if dict(data.dtypes)[col_name] != 'int':
    data = data.withColumn(col_name, replace(col(col_name), "NA"))
  

In [48]:
data.describe().toPandas().transpose()

0                   1  ...            3         4
summary        count                mean  ...          min       max
Ob             12745              6373.0  ...            1     12745
WageNew        12745  11432.671479011377  ...            6    650305
Age            12745  25.048646528050217  ...           16        44
Nationality    12745                None  ...  Afghanistan  Zimbabwe
...              ...                 ...  ...          ...       ...
GKDiving       12707  16.684347210199103  ...            1        90
GKHandling     12707   16.43920673644448  ...            1        92
GKKicking      12707  16.274887857086647  ...            1        91
GKPositioning  12707  16.444558117572992  ...            1        90
GKReflexes     12707   16.76989061147399  ...            1        94

[81 rows x 5 columns]

In [49]:
data.select([count(when (isnan(c) | col(c).isNull(), c)).alias(c) for c in data.columns]).show()

+---+-------+---+-----------+-------+---------+----+-------+--------------+------------------------+---------+-----------+---------+---------+---------+--------+------+--------------------+------+------+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+--------+---------+---------------+------------+-------+---------+-----+----------+-----------+-----------+------------+-----------+-------+---------+-------+---------+-------+-------+--------+---------+----------+-------------+-----------+------+---------+---------+-------+--------------+-------------+--------+----------+---------+-------------+----------+
| Ob|WageNew|Age|Nationality|Overall|Potential|Club|Special|Preferred Foot|International Reputation|Weak Foot|Skill Moves|Work Rate|Body Type|Real Face|Position|Joined|Contract Valid Until|Height|Weight|  LS|  ST|  RS|  LW|  LF|  CF|  RF|  RW| LAM| CAM| RAM|  LM| LCM|  CM| RCM|  RM| LWB| LDM| CDM| RDM| RWB

In [ ]:
data = data.drop('Market Category')
data = data.na.drop()
print (data.count(), len(data.columns))

11812 15


In [ ]:
assembler =  VectorAssembler(inputCols=['Year', 'Engine HP', 'Engine Cylinders', 'Number of Doors', 'highway MPG', 'city mpg', 'Popularity'],
                             outputCol='Attributes')
regressor = RandomForestRegressor(featuresCol='Attributes', labelCol='MSRP')
pipeline = Pipeline(stages=[assembler, regressor])
pipeline.write().overwrite().save("pipeline")
!ls

'data (1).csv'	 spark-2.4.7-bin-hadoop2.7
 data.csv	 spark-2.4.7-bin-hadoop2.7.tgz
 pipeline	 spark-2.4.7-bin-hadoop2.7.tgz.1
 sample_data


In [ ]:
pipelineModel = Pipeline.load("pipeline")
paramGrid = ParamGridBuilder() \
  .addGrid(regressor.numTrees, [100, 500]) \
  .build()
crossval = CrossValidator(estimator=pipelineModel,
                          estimatorParamMaps = paramGrid,
                          evaluator=RegressionEvaluator(labelCol="MSRP"),
                          numFolds=5)

In [ ]:
train_data, test_data = data.randomSplit([0.8, 0.2], seed = 101)
cvModel = crossval.fit(train_data)

In [ ]:
bestModel = cvModel.bestModel
for x in range(len(bestModel.stages)):
  print(bestModel.stages[x])

VectorAssembler_86b184f1d251
RandomForestRegressionModel (uid=RandomForestRegressor_3d04e9c36ca7) with 500 trees


In [ ]:
pred = cvModel.transform(test_data)
pred.select("MSRP", 'prediction').show()

+-----+------------------+
| MSRP|        prediction|
+-----+------------------+
|30550|  37891.5375249605|
|32700| 37910.65412559051|
|29350|28089.048450251677|
|34890| 27567.21209179562|
|27990| 27567.21209179562|
|29990| 27567.21209179562|
| 3381| 6333.026247122154|
| 3130| 5075.015051031231|
| 3222| 4973.930524592439|
| 2000| 4931.684684055391|
| 2060| 4923.682955701523|
| 2042|4895.7338215567315|
| 2181| 4967.793060608286|
| 2066| 5307.137028544619|
| 2265| 4974.509202636521|
|43015|  39947.6457880624|
|49440|  39947.6457880624|
|45950| 39876.37884105684|
|89000|37087.655916152755|
|89000| 37123.14968684864|
+-----+------------------+
only showing top 20 rows



In [ ]:
eval = RegressionEvaluator(labelCol = 'MSRP')
rmse = eval.evaluate(pred)
mse = eval.evaluate(pred, {eval.metricName: "mse"})
mae = eval.evaluate(pred, {eval.metricName: "mae"})
r2 = eval.evaluate(pred, {eval.metricName: "r2"})

print("RMSE %.3f" %rmse)
print("MSE %.3f" %mse)
print("MAE %.3f" %mae)
print("R2 %.3f" %r2)

RMSE 22805.375
MSE 520085114.494
MAE 8806.961
R2 0.873
